In [1]:
!pip install datasets ipywidgets transformers[torch] evaluate scikit-learn ray[tune] wandb hyperopt

In [2]:
import huggingface_hub
huggingface_hub.login()

In [3]:
%env WANDB_PROJECT=OO_Fine_Tune
%env WANDB_NOTEBOOK_NAME=/home/ed/Downloads/OO-Fine-Tune/OO_Fine_Tune.ipynb
%env WANDB_LOG_MODEL=off # this is slow for sweeps

env: WANDB_PROJECT=OO_Fine_Tune
env: WANDB_NOTEBOOK_NAME=/home/ed/Downloads/OO-Fine-Tune/OO_Fine_Tune.ipynb
env: WANDB_LOG_MODEL=off # this is slow for sweeps


In [4]:
import datasets
from transformers import AutoModelForSequenceClassification

# Configs
model_name = "huggingface/CodeBERTa-small-v1"
exp_name = "oo-method-test-model-bylibrary"
#train_size = "[:1%]"
quick_test_percent = 1.0
eval_steps = 0.2
save_steps = 0.2
push = False
hyperopt = True
if hyperopt: push = False
early_patience = 10 if hyperopt else 5
resume = False

train_split = f"train"

id2label = {0: "func", 1: "method"}
label2id = {"func": 0, "method": 1}

def model_init():
    global best_accuracy
    best_accuracy = 0.0
    return AutoModelForSequenceClassification.from_pretrained(model_name,
                                                             id2label=id2label,
                                                             label2id=label2id,
                                                             num_labels=2)

model = model_init()

small_ds_train = datasets.load_dataset("ejschwartz/oo-method-test-split", "bylibrary", split=train_split)
ds_dev = datasets.load_dataset("ejschwartz/oo-method-test-split", "bylibrary", split="test")
small_ds_dev = ds_dev.shuffle(seed=42).select(range(round(len(ds_dev) * quick_test_percent)))

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at huggingface/CodeBERTa-small-v1 and are newly initialized: ['classifier.out_proj.weight', 'classifier.out_proj.bias', 'classifier.dense.bias', 'classifier.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [5]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name)

def tokenize_function(examples):
    return tokenizer(examples["Disassembly"], padding="max_length", truncation=True)

small_ds_train = small_ds_train.map(tokenize_function, batched=True, num_proc=8).rename_column("Disassembly", "text").rename_column("Type", "label")
small_ds_dev = small_ds_dev.map(tokenize_function, batched=True, num_proc=8).rename_column("Disassembly", "text").rename_column("Type", "label")
ds_dev = ds_dev.map(tokenize_function, batched=True, num_proc=8).rename_column("Disassembly", "text").rename_column("Type", "label")


Map (num_proc=8):   0%|          | 0/2836 [00:00<?, ? examples/s]

In [6]:
import transformers
import numpy as np

data_collator = transformers.DataCollatorWithPadding(tokenizer=tokenizer)

training_args = transformers.TrainingArguments(output_dir=exp_name,
                                  #auto_find_batch_size=True,
                                  per_device_train_batch_size=8,
                                  per_device_eval_batch_size=8,
                                  learning_rate=0.00000245415537008783,
                                  max_steps=887,
                                  logging_first_step=True,
                                  evaluation_strategy="steps",
                                  #eval_steps=eval_steps,
                                  eval_steps=eval_steps,
                                  logging_steps=eval_steps,
                                  save_steps=save_steps,
                                  push_to_hub=push,
                                  report_to="wandb",
                                  run_name=exp_name,
                                  save_total_limit=0,
                                  load_best_model_at_end=True,
                                  metric_for_best_model="eval_accuracy",
                                  lr_scheduler_type="cosine",
                                  warmup_ratio=0.05,
                                  num_train_epochs=0.2,
                                  )

import evaluate

metric = evaluate.load("accuracy")

def compute_metrics(eval_pred):
  global best_accuracy
  logits, labels = eval_pred
  predictions = np.argmax(logits, axis=-1)
  metrics = metric.compute(predictions=predictions, references=labels)
  metrics['best_accuracy'] = max(best_accuracy, metrics['accuracy'])
  best_accuracy = metrics['best_accuracy']
  return metrics

total_steps = len(small_ds_train) // training_args.per_device_train_batch_size * training_args.num_train_epochs
#optimizer = transformer
#scheduler = transformers.get_cosine_schedule_with_warmup(num_warmup_steps=total_steps*0.05, num_training_steps=total_steps)

trainer = transformers.Trainer(
    model_init=model_init,
    #model=model,
    args=training_args,
    tokenizer=tokenizer,
    train_dataset=small_ds_train,
    eval_dataset=small_ds_dev,
    compute_metrics=compute_metrics,
    callbacks = [transformers.EarlyStoppingCallback(early_stopping_patience=early_patience)],
    data_collator=data_collator
)

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at huggingface/CodeBERTa-small-v1 and are newly initialized: ['classifier.out_proj.weight', 'classifier.out_proj.bias', 'classifier.dense.bias', 'classifier.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [10]:
from ray import tune
import ray
import ray.tune.schedulers
import ray.tune.search.hyperopt
import ray.tune.progress_reporter

def wandb_hp_space(trial):
    return {
        "method": "bayes",
        # why do we need this and the metric arg to hyperparameter_search?
        "metric": {"name": "eval/accuracy", "goal": "maximize"},
        "parameters": {
            "learning_rate": {"distribution": "log_uniform_values" if False else "uniform", "min": 1e-6, "max": 1e-4},
            #"per_device_train_batch_size": {"values": [4, 8]},
            "max_steps": {"distribution": "uniform", "min": 1, "max": 1000},
            #"num_train_epochs": {"distribution": "uniform", "min": 0.1, "max": 4},
            #"lr_scheduler_type": {"values": ["linear", "cosine"]},
            #"warmup_ratio": {"distribution": "uniform", "min": 0.0, "max": 0.25},
            #"fp16": {"values": [True, False]},
        },
        "early_terminate": {
            "type": "hyperband",
            "min_iter": 3,
            "eta": 2
        }
    }

def ray_hp_space(trial):
    return {
            "learning_rate": ray.tune.loguniform(1e-6, 1e-4),
            "num_train_epochs": ray.tune.uniform(0.1, 4),
            # choices don't work with PBT
            #"lr_scheduler_type": ray.tune.choice(["linear", "cosine"]),
            "warmup_ratio": ray.tune.uniform(0.0, 0.25),
            #"fp16": ray.tune.choice([True, False]),
        }

if hyperopt:
    best = trainer.hyperparameter_search(
        direction="maximize", 
        backend="wandb",
        hp_space=wandb_hp_space,
        #backend="ray",
        #hp_space=ray_hp_space,
        progress_reporter=ray.tune.progress_reporter.JupyterNotebookReporter(),
        metric="eval/accuracy",
        compute_objective=lambda d: d['eval_accuracy'],
        mode="max",
        n_trials=30, # number of trials
        #search_alg=ray.tune.search.hyperopt.HyperOptSearch(),
        #scheduler=ray.tune.schedulers.PopulationBasedTraining(hyperparam_mutations=ray_hp_space(None)),
        keep_checkpoints_num=1,
)
else:
    trainer.train(resume_from_checkpoint=resume)

Create sweep with ID: 1wpa6h8x
Sweep URL: https://wandb.ai/eschwartz/OO_Fine_Tune/sweeps/1wpa6h8x


wandb: Agent Starting Run: 97sjboe5 with config:
wandb: 	learning_rate: 3.662189175786302e-06
wandb: 	max_steps: 116.0448051231694


Trying to set _wandb in the hyperparameter search but there is no corresponding field in `TrainingArguments`.
Trying to set assignments in the hyperparameter search but there is no corresponding field in `TrainingArguments`.
Trying to set metric in the hyperparameter search but there is no corresponding field in `TrainingArguments`.
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at huggingface/CodeBERTa-small-v1 and are newly initialized: ['classifier.out_proj.weight', 'classifier.out_proj.bias', 'classifier.dense.bias', 'classifier.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


wandb: WARNING Ignored wandb.init() arg project when running a sweep.


wandb: WARNING Config item 'learning_rate' was locked by 'sweep' (ignored update).
wandb: WARNING Config item 'max_steps' was locked by 'sweep' (ignored update).


...

  0%|          | 0/355 [00:00<?, ?it/s]

{'eval_loss': 0.6618301272392273, 'eval_accuracy': 0.8423836389280677, 'eval_best_accuracy': 0.8423836389280677, 'eval_runtime': 46.016, 'eval_samples_per_second': 61.631, 'eval_steps_per_second': 7.715, 'epoch': 0.02}
{'loss': 0.147, 'learning_rate': 6.229453457049311e-06, 'epoch': 0.03}


  0%|          | 0/355 [00:00<?, ?it/s]

{'eval_loss': 0.7814058065414429, 'eval_accuracy': 0.8589562764456982, 'eval_best_accuracy': 0.8589562764456982, 'eval_runtime': 46.031, 'eval_samples_per_second': 61.611, 'eval_steps_per_second': 7.712, 'epoch': 0.03}
{'loss': 0.1676, 'learning_rate': 1.6786460476928193e-06, 'epoch': 0.05}


  0%|          | 0/355 [00:00<?, ?it/s]

In [11]:
#trainer.evaluate()
#trainer.evaluate(ds_dev)

In [13]:
import copy

if hyperopt:
    print(best)

    eval_training_args = copy.copy(training_args)
    for k, v in best.hyperparameters.items():
        if k == "max_steps": v = int(v)
        setattr(eval_training_args, k, v)

    eval_trainer = transformers.Trainer(
        model_init=model_init,
        #model=best,
        args=eval_training_args,
        tokenizer=tokenizer,
        train_dataset=small_ds_train,
        eval_dataset=ds_dev,
        compute_metrics=compute_metrics,
        #callbacks = [EarlyStoppingCallback(early_stopping_patience=3)],
        data_collator=data_collator,
    )
    eval_trainer.train()
    eval_trainer.evaluate()

BestRun(run_id='uakeqy2o', objective=0.9160789844851904, hyperparameters={'learning_rate': 2.386135927313411e-05, 'max_steps': 887.5577347480429, 'assignments': {}, 'metric': 'eval/accuracy'}, run_summary=None)


Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at huggingface/CodeBERTa-small-v1 and are newly initialized: ['classifier.out_proj.weight', 'classifier.out_proj.bias', 'classifier.dense.bias', 'classifier.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at huggingface/CodeBERTa-small-v1 and are newly initialized: ['classifier.out_proj.weight', 'classifier.out_proj.bias', 'classifier.dense.bias', 'classifier.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
wandb: WARNING Config item 'learning_rate' was locked by 'sweep' (ignored update).
wandb: WARNING Config item 'max_steps' was locked by 'sweep' (ignored update).


  0%|          | 0/887 [00:00<?, ?it/s]

{'loss': 0.7452, 'learning_rate': 5.302524282918692e-07, 'epoch': 0.0}
{'loss': 0.3788, 'learning_rate': 2.2422283922793875e-05, 'epoch': 0.02}


  0%|          | 0/355 [00:00<?, ?it/s]

...

  0%|          | 0/355 [00:00<?, ?it/s]

{'eval_loss': 0.4925839304924011, 'eval_accuracy': 0.8797602256699577, 'eval_best_accuracy': 0.8797602256699577, 'eval_runtime': 45.7725, 'eval_samples_per_second': 61.959, 'eval_steps_per_second': 7.756, 'epoch': 0.05}
{'loss': 0.1162, 'learning_rate': 2.4541553700878304e-06, 'epoch': 0.07}


  0%|          | 0/355 [00:00<?, ?it/s]

{'eval_loss': 0.3302706480026245, 'eval_accuracy': 0.9160789844851904, 'eval_best_accuracy': 0.9160789844851904, 'eval_runtime': 45.988, 'eval_samples_per_second': 61.668, 'eval_steps_per_second': 7.719, 'epoch': 0.07}
{'train_runtime': 525.5844, 'train_samples_per_second': 13.501, 'train_steps_per_second': 1.688, 'train_loss': 0.18107375216994775, 'epoch': 0.09}


  0%|          | 0/355 [00:00<?, ?it/s]

In [14]:
#AutoTokenizer.from_checkpoint("/home/ed/Downloads/OO-Fine-Tune/oo-method-test-model-bylibrary-1percent/run-uw5f4ld2/checkpoint-4000")
#if hyperopt:
#    tokenizer.push_to_hub("ejschwartz/oo-method-test-model-bylibrary-1percent")
#    checkpoint.push_to_hub("ejschwartz/oo-method-test-model-bylibrary-1percent")

In [16]:
print(eval_trainer.evaluate(ds_dev))

  0%|          | 0/355 [00:00<?, ?it/s]

{'eval_loss': 0.3302706480026245, 'eval_accuracy': 0.9160789844851904, 'eval_best_accuracy': 0.9160789844851904, 'eval_runtime': 43.8356, 'eval_samples_per_second': 64.696, 'eval_steps_per_second': 8.098, 'epoch': 0.09}


In [21]:
if push:
    # Re-evaluate on best model
    eval_trainer.push_to_hub(dataset="ejschwartz/oo-method-test-split", dataset_tags="ejschwartz/oo-method-test-split")

BadRequestError:  (Request ID: Root=1-64fdc2f9-2887e3e476651a1b59fdcebb;c77f2b96-7a33-42b9-820e-0bfed2e5e71e)

Bad request for commit endpoint:
"model-index[0].results[0].dataset.config" must be a string